In [16]:
import osmnx as ox
import geopandas as gpd
import networkx as nx
from shapely.geometry import Point
import numpy as np
import pandas as pd
import requests
import xml.etree.ElementTree as ET
import h3
from shapely import wkt
from shapely.geometry import box, Polygon
import folium
import os

# Load data
all_lts_df = pd.read_csv("/Users/leonardo/Desktop/Tesi/LTSBikePlan/data/Trento_all_lts.csv")
all_lts_df['geometry'] = all_lts_df['geometry'].apply(wkt.loads)
gdf_nodes = pd.read_csv("/Users/leonardo/Desktop/Tesi/LTSBikePlan/data/Trento_gdf_nodes.csv", index_col=0)
gdf_nodes['geometry'] = gdf_nodes['geometry'].apply(wkt.loads)

#Convert the DataFrame to a GeoDataFrame
all_lts = gpd.GeoDataFrame(all_lts_df, geometry='geometry')
all_lts.crs = "EPSG:32632"
all_lts_projected = all_lts.to_crs(epsg=4326)

nodes = gpd.GeoDataFrame(gdf_nodes, geometry='geometry')
nodes.crs = "EPSG:32632"
nodes_projected = nodes.to_crs(epsg=4326)

def classify_stress(row):
    if pd.notna(row['lts']):  # Checks if 'lts' value is not NaN
        if row['lts'] in [1, 2]:
            return 'low'
        elif row['lts'] in [3, 4]:
            return 'high'
    return None  # Returns None for NaN or unclassified values

# Apply the function to create 'type_stress' column
all_lts_projected['type_stress'] = all_lts_projected.apply(classify_stress, axis=1)
nodes_projected['type_stress'] = nodes_projected.apply(classify_stress, axis=1)

# Create a network
G = nx.Graph()
# Add nodes from nodes_projected
for idx, row in nodes_projected.iterrows():
    # Add node with attributes
    G.add_node(idx, **row.to_dict())

# Add edges from all_lts_projected
for _, row in all_lts_projected.iterrows():
    # Extract start and end node IDs
    u = row['u']
    v = row['v']
    # Add edge with attributes
    G.add_edge(u, v, **row.to_dict())

print(f"Number of nodes: {G.number_of_nodes()}")
print(f"Number of edges: {G.number_of_edges()}")

# Print node attributes
if G.number_of_nodes() > 0:
    first_node = next(iter(G.nodes))
    print("Node Attributes:", list(G.nodes[first_node].keys()))
else:
    print("No nodes in the graph.")

# Print edge attributes
if G.number_of_edges() > 0:
    first_edge = next(iter(G.edges))
    print("Edge Attributes:", list(G.edges[first_edge].keys()))
else:
    print("No edges in the graph.")

base_path = "/Users/leonardo/Desktop/Tesi/LTSBikePlan/images"
city_name = "Trento"

# Create the path for the new folder
city_folder_path = os.path.join(base_path, city_name)

# Create the folder if it doesn't exist
if not os.path.exists(city_folder_path):
    os.makedirs(city_folder_path)

# Number of nodes and edges before simplification
initial_node_count = G.number_of_nodes()
initial_edge_count = G.number_of_edges()

# Find isolated nodes
isolated_nodes = list(nx.isolates(G))
num_isolated_nodes = len(isolated_nodes)

print(f"Initial number of nodes: {initial_node_count}")
print(f"Initial number of edges: {initial_edge_count}")
print(f"Number of isolated nodes: {num_isolated_nodes}")

# Remove isolated nodes
G.remove_nodes_from(isolated_nodes)

# Number of nodes and edges after removing isolated nodes
final_node_count = G.number_of_nodes()
final_edge_count = G.number_of_edges()

print(f"Final number of nodes: {final_node_count}")
print(f"Final number of edges: {final_edge_count}")

Number of nodes: 20965
Number of edges: 12902
Node Attributes: ['y', 'x', 'street_count', 'highway', 'ref', 'geometry', 'lts', 'message', 'type_stress']
Edge Attributes: ['u', 'v', 'key', 'osmid', 'lanes', 'name', 'highway', 'maxspeed', 'geometry', 'length', 'rule', 'lts', 'group', 'slope', 'slope_class', 'lanes_assumed', 'maxspeed_assumed', 'message', 'short_message', 'type_stress']
Initial number of nodes: 20965
Initial number of edges: 12902
Number of isolated nodes: 9293
Final number of nodes: 11672
Final number of edges: 12902


In [19]:
from shapely.ops import unary_union

# Function to retrieve population data from OpenStreetMap
def get_osm_population(city_name):
    query = f"""
    [out:xml][timeout:25];
    area[name="{city_name}"]->.searchArea;
    (
      node["population"](area.searchArea);
      way["population"](area.searchArea);
      relation["population"](area.searchArea);
    );
    out body;
    """
    url = "https://overpass-api.de/api/interpreter"
    response = requests.get(url, params={'data': query})
    root = ET.fromstring(response.content)
    # Extract population data
    for element in root.iter('tag'):
        if element.attrib['k'] == 'population':
            return element.attrib['v']
    return "Population data not found"

total_city_population = int(get_osm_population("Trento"))

In [3]:
print("Starting process to generate city boundary...")
print("Simplifying geometries...")
simplified_geometries = all_lts_projected.geometry.simplify(tolerance=0.001)
print("Performing unary union on simplified geometries...")
simplified_union = unary_union(simplified_geometries)
print("Applying buffer...")
city_boundary = simplified_union.buffer(0.005)
print("City boundary generation completed.")
#city_boundary = simplified_geometry.unary_union.buffer(0.005)

Starting process to generate city boundary...
Simplifying geometries...
Performing unary union on simplified geometries...
Applying buffer...
City boundary generation completed.


In [20]:
# Function to create a hexagonal grid within the city boundaries
def create_hex_grid_within_city_bounds(city_boundary, resolution):
    hexagons = h3.polyfill(city_boundary.__geo_interface__, resolution, geo_json_conformant=True)

    filtered_hexagons = []
    for h in hexagons:
        hex_polygon = Polygon(h3.h3_to_geo_boundary(h, geo_json=True))
        if hex_polygon.intersects(city_boundary):
            filtered_hexagons.append(hex_polygon)

    hex_grid = gpd.GeoDataFrame([{'geometry': hexagon} for hexagon in filtered_hexagons])
    hex_grid.crs = 'EPSG:4326'

    return hex_grid

hex_grid_within_city = create_hex_grid_within_city_bounds(city_boundary, 9)
hex_grid_projected = hex_grid_within_city.to_crs('EPSG: 32632')

In [21]:
# Calculate area for each hexagon to distribute population
hex_grid_projected['area'] = hex_grid_projected['geometry'].area

# Distribute the city's population across the hexagons
hex_grid_projected['estimated_population'] = (hex_grid_projected['area'] / hex_grid_projected['area'].sum()) * total_city_population
hex_grid_projected = hex_grid_projected.to_crs('EPSG:4326')
projected_crs = 'EPSG:32632' 
all_lts_projected_crs = all_lts_projected.to_crs(projected_crs)

# Calculate centroids
centroids = all_lts_projected_crs.geometry.centroid
centroids = centroids.to_crs(epsg=4326)

# Get the center latitude and longitude for the map
center_lat, center_lon = centroids.iloc[0].y, centroids.iloc[0].x
hex_grid_geojson = hex_grid_projected.to_json()

# Function to retrieve building data 
def get_building_data(city_name):
    # Retrieve buildings from OSM within the city boundary
    buildings = ox.features_from_place(city_name, tags={'building': True})
    return buildings

# Retrieve building data for city
buildings = get_building_data("Trento, Italy")
buildings = buildings.to_crs(hex_grid_projected.crs)
hex_grid_projected.reset_index(inplace=True)
hex_grid_projected.rename(columns={'index': 'hex_index'}, inplace=True)
hex_grid_with_buildings = gpd.sjoin(hex_grid_projected, buildings, how='left', predicate='intersects')
building_counts = hex_grid_with_buildings.groupby('hex_index').size()
hex_grid_projected['building_count'] = hex_grid_projected['hex_index'].map(building_counts).fillna(0)

# Adjust population estimation based on building count: here => simple average of area-based and building-based estimates
hex_grid_projected['adjusted_population'] = hex_grid_projected.apply(
    lambda row: (row['estimated_population'] + row['building_count']) / 2, axis=1)
assert 'adjusted_population' in hex_grid_projected.columns, "Adjusted population column not found"

hex_grid_geojson = hex_grid_projected.to_crs(epsg=4326).to_json()

m = folium.Map(location=[center_lat, center_lon], zoom_start=13)

def color_function(feature):
    population = feature['properties']['adjusted_population']
    
    high_population_threshold = total_city_population * 0.02  # 2% of total population
    medium_population_threshold = total_city_population * 0.01  # 1% of total population

    if population > high_population_threshold:
        return '#ff0000'  # Red 
    elif population > medium_population_threshold:
        return '#ffff00'  # Yellow 
    else:
        return '#00ff00'  # Green 

folium.GeoJson(
    hex_grid_geojson,
    name='Hexagonal Grid',
    style_function=lambda feature: {
        'fillColor': color_function(feature),
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.5,
    }
).add_to(m)

# Add layer control and display the map
folium.LayerControl().add_to(m)

file_path = os.path.join(city_folder_path, 'popxgrid_map.html')

# Assuming 'accident_map' is a Folium Map object
m.save(file_path)


In [32]:
# Spatial join between hexagons and edges
edges_gdf = gpd.GeoDataFrame(all_lts_projected[['geometry', 'u', 'v', 'type_stress']], geometry='geometry')
hex_edges = gpd.sjoin(hex_grid_projected, edges_gdf, how='left', predicate='intersects')
# Group edges by hexagon using a list for column names
hexagon_edges = hex_edges.groupby('hex_index')[['u', 'v']].apply(lambda x: list(zip(x['u'], x['v'])))
# Remove hexagons with only NaN values in their edge list
filtered_hexagon_edges = {hex_id: edges for hex_id, edges in hexagon_edges.items() if not all(np.isnan(edge).any() for edge in edges)}

# Filtering is done by checking 'type_stress' for 'low'
hexagon_edges_low_stress = hex_edges[hex_edges['type_stress'] == 'low'].groupby('hex_index')[['u', 'v']].apply(lambda x: list(zip(x['u'], x['v'])))

# Remove hexagons with only NaN values in their edge list
filtered_hexagon_edges_low_stress = {hex_id: edges for hex_id, edges in hexagon_edges_low_stress.items() if not all(np.isnan(edge).any() for edge in edges)}

filtered_hexagon_edges_low_stress

{1: [(1363981974.0, 1363981877.0),
  (1363981877.0, 1363981974.0),
  (11173485720.0, 1278121739.0),
  (1278121739.0, 11173485720.0),
  (2387504510.0, 11182638877.0),
  (11182638877.0, 2387504510.0),
  (11167037423.0, 827411291.0),
  (827411291.0, 11167037423.0),
  (11171189484.0, 11171189472.0),
  (11171189472.0, 11171189484.0)],
 2: [(3819175109.0, 3819175106.0),
  (3819175106.0, 3819175109.0),
  (269196194.0, 7382711075.0),
  (7382711075.0, 269196194.0),
  (4778365982.0, 3819175106.0),
  (3819175106.0, 4778365982.0),
  (10785443804.0, 3819175106.0),
  (3819175106.0, 10785443804.0),
  (10785443803.0, 10785443804.0),
  (10785443804.0, 10785443803.0),
  (10785443804.0, 10785543005.0),
  (10785543005.0, 10785443804.0),
  (1150135423.0, 10785443804.0),
  (10785443804.0, 1150135423.0),
  (2894414793.0, 10785543005.0),
  (10785543005.0, 2894414793.0),
  (269196194.0, 1150135423.0),
  (1150135423.0, 269196194.0),
  (1828007978.0, 269196194.0),
  (269196194.0, 1828007978.0),
  (10785543005.0,

In [ ]:
# Create a KDTree for efficient nearest neighbor search
node_points = {node: Point(data['x'], data['y']) for node, data in G.nodes(data=True)}
node_tree = cKDTree([(point.x, point.y) for point in node_points.values()])

# Function to find the closest node to a given point
def find_closest_node(centroid):
    _, nearest_node_index = node_tree.query((centroid.x, centroid.y))
    return list(node_points.keys())[nearest_node_index]

# Find the representative node for each hexagon using KDTree
representative_nodes = {}
for hex_id, edges in filtered_hexagon_edges.items():
    hexagon_geometry = hex_grid_projected.loc[hex_grid_projected['hex_index'] == hex_id, 'geometry'].iloc[0]
    centroid = find_hexagon_centroid(hexagon_geometry)
    closest_node = find_closest_node(centroid)
    representative_nodes[hex_id] = closest_node

# Compute shortest paths
shortest_paths = {}
path_cache = {}
for hex_id, start_node in representative_nodes.items():
    shortest_paths[hex_id] = {}
    for target_hex_id, target_node in representative_nodes.items():
        if hex_id != target_hex_id:
            # Check if the path has already been calculated
            if (start_node, target_node) not in path_cache:
                if nx.has_path(G, start_node, target_node): 
                    path_length = nx.dijkstra_path_length(G, source=start_node, target=target_node, weight='length')
                    path_cache[(start_node, target_node)] = path_length
                else:
                    path_cache[(start_node, target_node)] = None
            shortest_paths[hex_id][target_hex_id] = path_cache[(start_node, target_node)]

# Print shortest paths
for hex_id, paths in list(shortest_paths.items())[:5]:
    print(f"Hexagon {hex_id} paths: {paths}")

In [37]:
hexagon_connections = {}
detour_threshold = 1.5
for hex_id in shortest_paths:
    hexagon_connections[hex_id] = {}
    for target_hex_id in shortest_paths[hex_id]:
        baseline_path_length = shortest_paths[hex_id][target_hex_id]
        low_stress_path_length = shortest_paths_low_stress[hex_id][target_hex_id]
        if low_stress_path_length is not None and (baseline_path_length is None or low_stress_path_length <= baseline_path_length * detour_threshold):
            hexagon_connections[hex_id][target_hex_id] = True
        else:
            hexagon_connections[hex_id][target_hex_id] = False

# hexagon_connections now contains information about which hexagons are connected via low-stress paths
hexagon_connections

{0: {1: False,
  2: True,
  4: False,
  5: False,
  6: False,
  7: False,
  9: True,
  10: True,
  14: False,
  15: False,
  17: True,
  18: False,
  19: False,
  20: True,
  21: True,
  22: False,
  23: True,
  25: True,
  26: False,
  27: False,
  28: True,
  29: False,
  30: False,
  31: False,
  32: False,
  34: False,
  36: True,
  37: True,
  39: True,
  40: False,
  42: False,
  43: False,
  44: True,
  45: False,
  46: True,
  49: True,
  50: False,
  51: False,
  52: True,
  54: False,
  55: True,
  57: False,
  58: False,
  59: True,
  60: False,
  62: False,
  63: True,
  66: False,
  67: False,
  69: False,
  71: False,
  74: False,
  76: False,
  79: False,
  81: True,
  83: False,
  84: True,
  85: False,
  87: False,
  88: False,
  89: False,
  90: False,
  92: False,
  93: False,
  95: False,
  96: False,
  98: False,
  99: False,
  101: True,
  102: True,
  103: False,
  104: False,
  106: False,
  107: True,
  110: True,
  111: False,
  113: False,
  116: True,
  119:

In [38]:
def query_osm_building_types(city_name, building_types):
    all_destinations = []
    for building_type in building_types:
        try:
            # Query OSM for the specified building type
            query = {'building': building_type}
            buildings = ox.features_from_place(city_name, tags=query)

            for idx, building in buildings.iterrows():
                destination = {
                    'name': building.get('name', 'Unknown'),
                    'type': building_type,
                    'coordinates': (building.geometry.centroid.y, building.geometry.centroid.x)
                }
                all_destinations.append(destination)
        except Exception as e:
            print(f"Error querying building type '{building_type}': {e}")

    return all_destinations

# Example usage
city_name = "Trento, Italy"
building_types = ['sports_centre', 'train_station', 'supermarket']
destinationz = query_osm_building_types(city_name, building_types)
destinationz

Error querying building type 'supermarket': There are no data elements in the server response. Check log and query location/tags.


[{'name': 'Palestra comunale',
  'type': 'sports_centre',
  'coordinates': (46.15191399681905, 12.658802885518611)},
 {'name': 'Unknown',
  'type': 'train_station',
  'coordinates': (46.14820112508989, 12.658817723519059)}]

In [39]:
import json

# Load the destinations category data
with open('destinations.json') as f:
    destinations_data = json.load(f)

# Extracting destination types
destination_types = []
for category in destinations_data['categories']:
    for dest_type in category['types']:
        destination_types.append(dest_type['type_name'])

def query_osm_for_destinations(city_name, dest_types):
    all_destinations = []
    for dest_type in dest_types:
        try:
            # Initially query with 'amenity' tag
            destinations = ox.features_from_place(city_name, tags={'amenity': dest_type})
            if not destinations.empty:
                for idx, row in destinations.iterrows():
                    all_destinations.append({
                        'name': row.get('name', 'Unknown'),
                        'type': dest_type,
                        'coordinates': (row.geometry.centroid.y, row.geometry.centroid.x)
                    })
            else:
                print(f"No data returned for destination type: {dest_type}")
        except Exception as e:
            print(f"Error querying {dest_type}: {e}")

    return all_destinations

city_name = "Trento, Italy"
list_destinations = query_osm_for_destinations(city_name, destination_types)
list_destinations = destinationz + list_destinations

# Associate destinations with hexagons
points_geometry = [Point(coord[1], coord[0]) for coord in [destination['coordinates'] for destination in list_destinations]]
gdf_destinations = gpd.GeoDataFrame(list_destinations, geometry=points_geometry)
gdf_destinations.crs = 'EPSG:4326'

# Ensure that CRS of both GeoDataFrames match
gdf_destinations = gdf_destinations.to_crs(hex_grid_projected.crs)

# Ensuring CRS match
gdf_destinations = gdf_destinations.to_crs(hex_grid_projected.crs)
print(gdf_destinations)
# Spatial join
joined_df = gpd.sjoin(hex_grid_projected, gdf_destinations, how='left', predicate='contains')
print(joined_df)
# Check for NaN values in the specified columns
nan_check = joined_df[['index_right', 'name', 'type', 'coordinates']].isna().all(axis=1).sum()
print(f"\nNumber of rows where 'index_right', 'name', 'type', 'coordinates' are all NaN: {nan_check}")

# Checking for non-NaN values
not_nan_check = joined_df[['index_right', 'name', 'type', 'coordinates']].dropna().shape[0]
print(f"\nNumber of rows with valid data in 'index_right', 'name', 'type', 'coordinates': {not_nan_check}")

Error querying doctors: There are no data elements in the server response. Check log and query location/tags.
Error querying dentist: There are no data elements in the server response. Check log and query location/tags.
Error querying hospital: There are no data elements in the server response. Check log and query location/tags.
Error querying train_station: There are no data elements in the server response. Check log and query location/tags.
Error querying nature_reserve: There are no data elements in the server response. Check log and query location/tags.
Error querying park: There are no data elements in the server response. Check log and query location/tags.
Error querying sports_centre: There are no data elements in the server response. Check log and query location/tags.
                                                 name           type  \
0                                   Palestra comunale  sports_centre   
1                                             Unknown  train_station 

In [43]:
# Function to check if a row represents a destination hexagon
def is_destination(row):
    return not pd.isna(row.get('index_right')) and not pd.isna(row.get('name')) and not pd.isna(row.get('type')) and not pd.isna(row.get('coordinates'))

# Identify destination hexagons
destination_hexagons = joined_df[joined_df.apply(is_destination, axis=1)]

# Reproject to a suitable projected CRS
projected_crs = 'EPSG:32632'  
joined_df = joined_df.to_crs(projected_crs)
joined_df['centroid'] = joined_df.geometry.centroid


print("Sample Destination Hexagons:")
print(destination_hexagons.head())

Sample Destination Hexagons:
     hex_index                                           geometry  \
124        124  POLYGON ((782136.839 5117831.287, 782156.037 5...   
130        130  POLYGON ((780626.545 5116717.167, 780645.725 5...   
203        203  POLYGON ((782400.646 5116969.693, 782419.846 5...   
225        225  POLYGON ((782434.055 5118472.993, 782453.256 5...   
225        225  POLYGON ((782434.055 5118472.993, 782453.256 5...   

              area  estimated_population  building_count  adjusted_population  \
124  106342.200398              8.009631              83            45.504815   
130  106343.155589              8.009702             100            54.004851   
203  106358.127581              8.010830              41            24.505415   
225  106335.570678              8.009131             151            79.504566   
225  106335.570678              8.009131             151            79.504566   

     index_right               name           type  \
124          9.

In [44]:
# Assuming G and G_low_stress graphs are already defined and loaded
import pyproj
from shapely.ops import transform

def transform_point_to_graph_crs(point, point_crs, graph_crs):
    """Transform a point from its original CRS to the CRS of the graph."""
    point_proj = pyproj.CRS(point_crs)
    graph_proj = pyproj.CRS(graph_crs)
    project = pyproj.Transformer.from_crs(point_proj, graph_proj, always_xy=True).transform
    return transform(project, point)

def nearest_node(G, point, point_crs='EPSG:32632', graph_crs='EPSG:4326'):
    """Find the nearest node in the graph to the given point."""
    transformed_point = transform_point_to_graph_crs(point, point_crs, graph_crs)
    min_distance = float('inf')
    nearest = None

    for node in G.nodes(data=True):
        node_point = Point(node[1]['x'], node[1]['y'])
        distance = transformed_point.distance(node_point)
        if distance < min_distance:
            nearest = node[0]
            min_distance = distance

    return nearest

def dijkstra_distance(G, source_geometry, target_geometry, point_crs='EPSG:32632', graph_crs='EPSG:4326'):
    source_node = nearest_node(G, source_geometry, point_crs, graph_crs)
    target_node = nearest_node(G, target_geometry, point_crs, graph_crs)
    try:
        distance = nx.dijkstra_path_length(G, source=source_node, target=target_node, weight='length')
    except nx.NetworkXNoPath:
        distance = float('inf')
    
    return distance

hexagon_destinations = {}

# Main loop for calculating accessible destinations
for index, hexagon in joined_df.iterrows():
    accessible_destinations = []
    for dest_index, destination in destination_hexagons.iterrows():
        if 'centroid' in hexagon and 'centroid' in destination:
            distance = dijkstra_distance(G, hexagon['centroid'], destination['centroid'])
            if distance <= 2000:  
                accessible_destinations.append((destination['name'], destination['type'], destination['geometry'], dest_index))

    hexagon_destinations[(index, hexagon['geometry'])] = {
        'total_number_of_destinations': len(accessible_destinations),
        'destinations': accessible_destinations
    }
#hexagon_destinations

In [45]:
# Second loop for G_low_stress graph
for index, hexagon in joined_df.iterrows():
    accessible_destinations_low = []
    for dest_index, destination in destination_hexagons.iterrows():
        # Ensure that centroid exists for both hexagon and destination
        if 'centroid' in hexagon and 'centroid' in destination:
            distance = dijkstra_distance(G_low_stress, hexagon['centroid'], destination['centroid'])

            if distance <= 2000: 
                accessible_destinations_low.append((destination['name'], destination['type'], destination['geometry'], dest_index))

    # Update the existing hexagon_destinations dictionary
    hexagon_destinations[(index, hexagon['geometry'])].update({
        'total_number_of_destinations_low': len(accessible_destinations_low),
        'destinations_low': accessible_destinations_low
    })

hexagon_destinations

{(0,
  <POLYGON ((784420.844 5109160.987, 784440.062 5108963.732, 784627.181 510889...>): {'total_number_of_destinations': 0,
  'destinations': [],
  'total_number_of_destinations_low': 0,
  'destinations_low': []},
 (1,
  <POLYGON ((782530.669 5110092.147, 782549.867 5109894.924, 782736.949 510982...>): {'total_number_of_destinations': 0,
  'destinations': [],
  'total_number_of_destinations_low': 0,
  'destinations_low': []},
 (2,
  <POLYGON ((783034.307 5110463.662, 783053.511 5110266.442, 783240.597 511019...>): {'total_number_of_destinations': 1,
  'destinations': [("Scuola dell'Infanzia di San Leonardo",
    'kindergarten',
    <POLYGON ((784545.207 5111578.206, 784564.428 5111380.997, 784751.528 511130...>,
    515)],
  'total_number_of_destinations_low': 0,
  'destinations_low': []},
 (3,
  <POLYGON ((784833.525 5108619.658, 784852.747 5108422.389, 785039.877 510834...>): {'total_number_of_destinations': 0,
  'destinations': [],
  'total_number_of_destinations_low': 0,
  'desti

In [46]:
# Load scoring processes
with open('bna_scoring.json') as file:
    scoring_data = json.load(file)

# Convert the JSON data into more accessible structures
destination_weights = {category['category_name']: category['weight'] for category in destinations_data['categories']}
type_weights = {dest_type['type_name']: dest_type['weight'] for category in destinations_data['categories'] for dest_type in category['types']}
scoring_processes = {process['process']: process['criteria'] for process in scoring_data['scoring_process']}

# Function to calculate score for a single destination type
def calculate_score_for_type(destinations, scoring_process):
    criteria = scoring_processes[scoring_process]
    score = 0
    for i, destination in enumerate(destinations):
        if i < len(criteria):
            score += criteria[i]['points']
    return score

# Score each hexagon
for hexagon, hex_data in hexagon_destinations.items():
    hex_scores = {}
    for category in destinations_data['categories']:
        cat_score = 0
        for dest_type in category['types']:
            type_name = dest_type['type_name']
            scoring_proc = dest_type['scoring_process']
            destinations = [d for d in hex_data['destinations'] if d[1] == type_name]
            type_score = calculate_score_for_type(destinations, scoring_proc)
            weighted_type_score = type_score * type_weights[type_name] / 100
            cat_score += weighted_type_score

        # Apply category weight
        weighted_cat_score = cat_score * destination_weights[category['category_name']] / 100
        hex_scores[category['category_name']] = weighted_cat_score

    hexagon_destinations[hexagon]['scores'] = hex_scores

for hexagon in hexagon_destinations:
    total_score = sum(hexagon_destinations[hexagon]['scores'].values())
    hexagon_destinations[hexagon]['total_score'] = total_score

# Iterate over hexagons to calculate total scores and overall score
overall_score = 0
total_population = sum(joined_df['adjusted_population'])

for index, hexagon in joined_df.iterrows():
    hex_population = hexagon['adjusted_population']
    hex_key = (index, hexagon['geometry'])
    hex_data = hexagon_destinations.get(hex_key, {})
    hex_score = hex_data.get('total_score', 0)  # Get the total score for the hexagon

    # Weight the hexagon's score by its population and add to overall score
    weighted_score = hex_score * (hex_population / total_population)
    overall_score += weighted_score

# Print the final overall score
print(f"Overall Score: {overall_score}")

Overall Score: 8.858542651253153


In [48]:
import branca.colormap as cm

hex_dest_data = [{'geometry': hex_geom, 'total_score': hex_data['total_score']} 
                 for (_, hex_geom), hex_data in hexagon_destinations.items()]

hex_dest_gdf = gpd.GeoDataFrame(hex_dest_data, crs='EPSG:32632')

hex_dest_gdf_projected = hex_dest_gdf.to_crs('EPSG:4326')
center_lat = hex_dest_gdf_projected.geometry.apply(lambda geom: geom.centroid.y).mean()
center_lon = hex_dest_gdf_projected.geometry.apply(lambda geom: geom.centroid.x).mean()

# Create a base folium map
m = folium.Map(location=[center_lat, center_lon], zoom_start=13)


# Function to determine the color of a hexagon based on its total_score
def get_hexagon_color(total_score):
    # You can adjust the color scheme based on your preference and scoring scale
    if total_score > 20:
        return 'green'
    elif total_score > 10:
        return 'orange'
    elif total_score > 5:
        return 'red'
    else:
        return 'darkred'

legend_colormap = cm.LinearColormap(
    colors=['darkred', 'red', 'orange', 'green'],
    index=[0, 5, 10, 20],
    vmin=0,
    vmax=20,
    caption='Total Score'
)

legend_colormap.add_to(m)

for _, row in hex_dest_gdf_projected.iterrows():
    color = get_hexagon_color(row['total_score'])
    folium.GeoJson(
        row['geometry'],
        style_function=lambda _, color=color: {
            'fillColor': color,
            'color': 'black',
            'weight': 1,
            'fillOpacity': 0.7
        }
    ).add_to(m)

file_path = os.path.join(city_folder_path, 'bna_score_map.html')

# Assuming 'accident_map' is a Folium Map object
m.save(file_path)

m